In [43]:
#--------------------------------------------------------------#
#                   Importação de Bibliotecas
#--------------------------------------------------------------#
import collections
import warnings
import pandas as pd
import numpy as np
from datetime import datetime 
import time
import matplotlib.pyplot as plt
import datetime
# Install a pip package in the current Jupyter kernel
import sys
!{sys.executable} -m pip install seaborn
!{sys.executable} -m pip install imblear
!{sys.executable} -m pip install tensorflow_addons

import seaborn as sns
#import imblearn
import tensorflow_addons as tfa
#from imblearn.over_sampling import SMOTE
#from imblearn.over_sampling import ADASYN

#--------------------------------------------------------------#
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score
from sklearn.tree import DecisionTreeClassifier
from sklearn.dummy import DummyClassifier
from sklearn.tree import export_graphviz
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import cross_validate
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import cross_val_predict
from sklearn.naive_bayes import MultinomialNB
from sklearn.ensemble import AdaBoostClassifier
from sklearn.svm import SVC
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.utils.class_weight import compute_class_weight
from sklearn.metrics import f1_score

#--------------------------------------------------------------#
import tensorflow as tf
from tensorflow import keras
from keras.models import Sequential
from keras.layers import Dense
from scikeras.wrappers import KerasClassifier, KerasRegressor
#from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
#from tensorflow.keras.layers import Dropout
from keras.constraints import maxnorm
from tensorboard.plugins.hparams import api as hp
import tensorflow_addons as tfa
#--------------------------------------------------------------#
import nengo
import nengo_dl
import keras_spiking
import nengo_loihi

#warnings.simplefilter("ignore")
#tf.get_logger().addFilter(lambda rec: "Tracing is expensive" not in rec.msg)


[notice] A new release of pip is available: 23.3.2 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip
ERROR: Could not find a version that satisfies the requirement imblear (from versions: none)
ERROR: No matching distribution found for imblear

[notice] A new release of pip is available: 23.3.2 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.2 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [48]:
#--------------------------------------------------------------#
#                Declaração de Funções/Métodos
#--------------------------------------------------------------#

# Função para criar o modelo, requerido pelo KerasClassifier
def create_model(init_mode='glorot_uniform', activation = 'softmax',
                 loss = ['categorical_crossentropy'], dropout_rate=0.0,
                 weight_constraint=1                 
                 ):  
  
  global layer1, layer2, layer3, layer4, layerX
  
  layer1 = tf.keras.layers.Dense(128, input_dim = 3, activation = 'relu', kernel_constraint=maxnorm(weight_constraint), name="layer1")
  layer2 = tf.keras.layers.Dropout(dropout_rate, name="layer2")
  layer3 = tf.keras.layers.Dense(64, activation = 'relu', kernel_constraint=maxnorm(weight_constraint), name="layer3")
  layer4 = tf.keras.layers.Dense(3, activation = activation, name="layer4")
  layerX = tf.keras.layers.BatchNormalization(momentum=0.99)
  
  model = Sequential([layer1, layer2, layer3, layer4, layerX])

  # Antes de treinarmos o modelo, é necessário compilarmos com o otimizador e a função de perda
  model.compile(optimizer = 'adam', loss = loss, metrics = ['accuracy'])
  
  return model

In [ ]:
from time import sleep

# Test Conversion
model = create_model()
model.summary()

converter = nengo_dl.Converter(model, swap_activations={tf.keras.activations.relu: nengo.SpikingRectifiedLinear()})
sleep(3)

# Test neuron type converter
net = converter.net
for ensemble in net.ensembles: print(ensemble, ensemble.neuron_type)

sleep(3)    
assert converter.verify(training=False, inputs=None, atol=1e-08, rtol=1e-05) #--> default arguments
sleep(3)
print('=> Return Verify: ', converter.verify(), ' <= ')
sleep(3)


Model: "sequential_33"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 layer1 (Dense)              (None, 128)               512       
                                                                 
 layer2 (Dropout)            (None, 128)               0         
                                                                 
 layer3 (Dense)              (None, 64)                8256      
                                                                 
 layer4 (Dense)              (None, 3)                 195       
                                                                 
 batch_normalization_29 (Bat  (None, 3)                12        
 chNormalization)                                                
                                                                 
Total params: 8,975
Trainable params: 8,969
Non-trainable params: 6
___________________________________________________

C:\Users\zanon\AppData\Local\Programs\Python\Python39\lib\site-packages\nengo_dl\converter.py:324: UserWarning: layer1.kernel_constraint has value <keras.constraints.MaxNorm object at 0x0000023602FE0430> != None, which is not supported (unless inference_only=True). Falling back to TensorNode.
  warnings.warn(
C:\Users\zanon\AppData\Local\Programs\Python\Python39\lib\site-packages\nengo_dl\converter.py:324: UserWarning: layer3.kernel_constraint has value <keras.constraints.MaxNorm object at 0x000002367EF2F3A0> != None, which is not supported (unless inference_only=True). Falling back to TensorNode.
  warnings.warn(
